In [1]:
from bs4 import BeautifulSoup
from bs4.element import NavigableString
import requests
import lxml

def crawl_naver_one(url):
    try:
        Access_header = {'User-Agent':'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/86.0.4240.80 Safari/537.36 Edg/86.0.622.48'}
        respond = requests.get(url,headers = Access_header)
        soup = BeautifulSoup(respond.text,'lxml')
        
        Title = soup.select_one('#articleTitle').get_text()
        Date = soup.select_one('.t11').get_text()
        Paper = soup.find("meta", property ="me2:category1").get('content')
        URL = soup.select('#main_content > div.article_header > div.article_info > div > a')[0].get('href')
        
        source = soup.select('#articleBodyContents')[0]
        contents = ""
        for src in source:
            if(type(src) == NavigableString and src):
                contents = contents + src
        contents = contents.replace("\n", '')
        contents = contents.replace("\u200b", '')
        
        Category = []
        for cate in soup.find_all('em','guide_categorization_item'):
            Category.append(cate.get_text())
        
        if len(Category) == 1:
            Category.append("")
        
        return Title,Date,contents,Category[0],Category[1],Paper,URL
    
    except ConnectionError:
        print(repond.statue_code)
        return
    
def crawl_URL_each(Sid1,Sid2,Date,Page_number):
    try:
        url = 'https://news.naver.com/main/list.nhn?mode=LS2D&listType=title&sid1={sid1}&sid2={sid2}&date={date}&page={number}'.format(sid1=Sid1,sid2=Sid2,date=Date,number=Page_number)
        Access_header = {'User-Agent':'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/86.0.4240.80 Safari/537.36 Edg/86.0.622.48'}
        respond = requests.get(url,headers = Access_header)
        soup = BeautifulSoup(respond.text,'lxml')
        Url_List = []
        
        if soup.select_one('#main_content > div.paging > strong').get_text() != str(Page_number): # 페이지 목록의 끝에 도달 시
            return False
        
        for art in soup.select('#main_content > div.list_body.newsflash_body > ul > li > a'):
            Url_List.append(art.get('href'))
            
        return Url_List
    
    except ConnectionError:
        print(respond.status_code)
        return
            
        

In [2]:
import datetime

def get_today():
    today = datetime.date.today()
    today = str(today).replace('-','')
    return today

def get_yesterday(today):
    if len(today)!=8:
        print("Date input Error")
        return
    d = datetime.date(int(today[0:4]),int(today[4:6]),int(today[6:8]))
    y = d - datetime.timedelta(1)
    y = str(y).replace('-','')
    
    return y

In [3]:
import sqlite3

def Create_Table(Table_name):
    conn = sqlite3.connect("database.db")
    cursor = conn.cursor()
    
    sql = "CREATE TABLE {table}(Title Text, Date VARCHAR(20), Contents Text, Category1 VARCHAR(8), Category2 VARCHAR(8), Paper VARCHAR(10), URL Text)".format(table=Table_name)
    try:
        cursor.execute(sql)
        
    except:
        return
    
    else:
        conn.commit()
        conn.close()
        return

def Input_Article(article, Table):
    if len(article) != 7:
        print("input Error")
        return
    conn = sqlite3.connect("database.db")
    cursor = conn.cursor()
    sql = "INSERT INTO {table} VALUES('{title}','{date}','{contents}','{cat1}','{cat2}','{paper}','{url}')".format(table=Table,title=article[0],date=article[1],contents=article[2],cat1=article[3],cat2=article[4],paper=article[5],url=article[6])
    print(sql)
    try:
        cursor.execute(sql)
        conn.commit()
        print("입력 성공")
        
    except:
        print("입력 실패")
        return

In [4]:
import time

def crawl_all_night(Sid1, Sid2, Max_Date, Table_name):
    
# sid1 = 100 : 정치
#  sid2 = 264: 청와대, 265: 국회, 정당, 266: 행정, 267: 국방/외교, 268: 북한, 269: 정치 일반
# sid1 = 101 : 경제
#  sid2 = 260: 부동산, 259: 금융, 258: 증권, 261: 산업/재계, 262: 글로벌경제, 263: 경제 일반, 771: 중소기업/벤처 
# sid1 = 102 : 사회
#  sid2 = 249: 사건사고, 250: 교육, 251: 노동, 252: 환경, 254: 언론, 59b: 인권/복지, 256: 지역, 276: 인물, 257: 사회 일반
# sid1 = 103 : 생활/문화
#  sid2 = 237: 여행/레저, 239: 자동차/시승기, 240: 도로/교통, 241: 건강정보, 242: 공연/전시, 243: 책, 244: 종교, 245: 생활/문화 일반 
# sid1 = 104 : 세계
#  sid2 = 231: 아시아/호주, 232: 미국/중남미, 233: 유럽, 234: 중동/아프리카, 64f: 영문, 71a: 일문
# sid1 = 105 : IT/과학
#  sid2 = 226: 인터넷, 228: 과학 일반. 229: 게임/리뷰, 283: 컴퓨터, 230: IT 일반
    Date = get_today()
    Create_Table(Table_name)
    
    while Max_Date > 0:
        Page_number = 1
        while True:
            List = crawl_URL_each(Sid1,Sid2,Date,Page_number)
            
            if List == False:
                break
                
            else:
                for url in List:
                    try:
                        art = crawl_naver_one(url)
                        Input_Article(art,Table_name)
                    except:
                        try:
                            time.sleep(0.01)
                            Input_Article(art,Table_name)
                        except:
                            pass
                Page_number = Page_number+1
        Date = get_yesterday(Date)
        Max_Date = Max_Date - 1
            
    print("End!")
    
    
    

In [ ]:
crawl_all_night(100,269,5,'일반')

INSERT INTO 일반 VALUES('"업체 반발할까 봐" 환경호르몬 검출 알고도 공개 안 해','2020.10.23. 오전 2:25','		<앵커>한국소비자원이 국내 자동차 업체의 승용차 좌석 커버에서 다량의 환경호르몬을 검출했는데, 이걸 2년 동안이나 공개하지 않은 사실이 확인됐습니다. 자동차 업체들이 반발할 게 뻔하고, 소송도 걱정돼서 그랬다는데, 그렇다면 소비자원은 왜 있는 걸까요?고정현 기자입니다.<기자>승용차의 좌석 커버를 칼로 잘라보니, 인조가죽 부분이 드러납니다.한국소비자원이 2년 전, 국내 5개 자동차업체 승용차의 순정 제품 좌석 커버를 대상으로 실험을 진행한 결과, 인조가죽으로 만든 4개 업체 좌석 커버에서 프탈레이트계 가소제가 검출됐습니다.인체에 들어가면 호르몬 작용을 교란시키는 환경호르몬으로, 특히 영유아나 어린이들에게 위험해 경구용 완구 같은 제품의 경우, 중량 대비 함유량이 0.1%가 넘지 않도록 엄격히 사용이 제한되고 있습니다.당시 확인된 프탈레이트계 가소제는 어린이 제품 사용 제한 기준과 비교해 250배에서 최대 300배나 됐습니다.하지만, 좌석 커버에 대해서는 법적 사용 제한 기준이 없는 실정입니다.[계명찬/한양대 생명과학과 교수 : 하절기에는 피부를 노출 시키고 다니잖아요. 자동차 승차할 때도 그렇고. 피부를 통해서 들어온 (환경호르몬은) 오래 (인체에) 남아요.]소비자원은 "내장재 유해물질 함량 기준이 없어 프탈레이트계 가소제가 제한 없이 사용되고 있는 것으로 추정된다"고 평가하면서도 실험 결과를 공개하지는 않았습니다.소비자원은 당시 실험이 공표를 염두에 둔 게 아니었고, 규제 기준이 없는 상황에서 검출 사실만 발표하면 자동차 업체들이 반발하며 소송을 걸어올 거라고 우려돼 비공개했다고 해명했습니다.하지만, 소비자원은 지난 2018년 12월, 자동차 핸들 커버에서 환경호르몬이 검출됐다는 사실은 보도자료를 통해 공개한 바 있습니다.고정현 기자(yd@sbs.co.kr)','정치','','SBS','https://news.sbs.

입력 성공
INSERT INTO 일반 VALUES('국감 마치고 국회 떠나는 윤석열 검찰총장','2020.10.23. 오전 1:29','[서울=뉴시스]김선웅 기자 = 윤석열 검찰총장이 23일 서울 여의도 국회에서 열린 법제사법위원회의 대검찰청에 대한 국정감사를 마친 후 국회를 나서고 있다. (공동취재사진) 2020.10.23.photo@newsis.com 공감언론 뉴시스가 독자 여러분의 소중한 제보를 기다립니다. 뉴스 가치나 화제성이 있다고 판단되는 사진 또는 영상을 뉴시스 사진영상부(n-photo@newsis.com)로 보내주시면 적극 반영하겠습니다.<ⓒ 공감언론 뉴시스통신사. 무단전재-재배포 금지>	','정치','사회','뉴시스','http://www.newsis.com/view/?id=NISI20201023_0016810356')
입력 성공
INSERT INTO 일반 VALUES('15시간 국감 마친 윤석열 검찰총장','2020.10.23. 오전 1:29','    (서울=연합뉴스) 안정원 기자 = 윤석열 검찰총장이 23일 국회 법제사법위원회 대검찰청 국정감사를 마친 뒤 국회를 나서고 있다. 2020.10.23    jeong@yna.co.kr<저작권자(c) 연합뉴스(https://www.yna.co.kr/), 무단 전재-재배포 금지>	','정치','사회','연합뉴스','http://yna.kr/PYH20201023002200013?did=1196m')
입력 성공
INSERT INTO 일반 VALUES('15시간 국감 마친 윤석열 검찰총장','2020.10.23. 오전 1:29','    (서울=연합뉴스) 안정원 기자 = 윤석열 검찰총장이 23일 국회 법제사법위원회 대검찰청 국정감사를 마친 뒤 국회를 나서고 있다. 2020.10.23    jeong@yna.co.kr<저작권자(c) 연합뉴스(https://www.yna.co.kr/), 무단 전재-재배포 금지>	','정치','사회','연합뉴스','http://yna.kr/PYH20201023002100013

INSERT INTO 일반 VALUES('윤석열 “퇴임후 국민에 어떻게 봉사할지 생각해보겠다”','2020.10.23. 오전 1:15','										윤석열 검찰총장은 23일 새벽까지 계속된 대검찰청에 대한 국회 법제사법위원회의 국정감사에서 퇴임 후 거취를 묻는 질의에 “우리 사회와 국민들을 위해 어떻게 봉사할지 그 방법을 천천히 생각해보겠다”고 말했다. 윤 총장이 퇴임 후 거취에 대한 생각을 밝힌 것은 이번이 처음이다.국민의힘 김도읍 의원은 이날 국정감사 마지막 질의에서 윤 총장에게 “지금 언론에 대통령 후보로 여론조사까지 되고 있다”며 “(검찰총장) 임기 마치고 정치를 하려는 마음이 있느냐”고 물었다.윤 총장은 잠시 침묵하다가 “지금 제 직무를 다 하는 것만으로도 다른 생각을 할 겨를이 없고, 향후 거취에 대해서 이야기하는 것도 적절하지 않다”고 답했다.이어서 “다만 소임을 다 마치고 나면, 저도 지금까지 살아오면서 우리 사회의 많은 혜택을 받은 사람이기 때문에 우리 사회와 국민들을 위해서 어떻게 봉사할지, 그런 방법은 천천히 한번 생각해보겠다”고 했다.김 의원은 “'그런 방법'에 정치도 들어가느냐”고 다시 물었다. 윤 총장은 “그것은 말씀드리기 어렵다”고 했다.다음은 김 의원과 윤 총장의 질의응답 전문. 총장님, 지금 대검 주변에 소위 총장님 응원하는 화환들이 몇 개쯤 있습니까? 글쎄, 뭐 아침에 찾아보니까 많이 있는 것 같은데 세어보진 않았습니다.150개쯤 있다는데요, 어떻게 생각하십니까? 하여튼 그분들 제가 그 뜻을 생각해서 해야 될 일 열심히 하겠습니다.오늘 이 국감장 안에 의원이 18명이 있어요. 여기에 민주당 의원들 대부분이 포함돼 있는데 일곱 분이 6월부터 지금까지 줄곧 윤석열 총장 사퇴하라, 거취 결정하라, 이렇게 주장했던 분들 사이에서 어제 아침 10시부터 익일 1시 정도까지 국정감사 받는다고 수고는 많이 하셨습니다. 대통령께서도 소임을 다하라고 하셨고 본인도 사퇴하지 않겠다고 하셨는데, 지금 언론에 대통령 후보로 여론조사까지 되고 있

INSERT INTO 일반 VALUES('북 피살 공무원 형, 해경 ‘월북 시도’ 발표에 “명예·인격 살인”','2020.10.23. 오전 12:36',' 북한군에 피살된 해양수산부 공무원 이 모 씨의 형 이래진 씨는 '이 씨가 채무에 시달리다 월북을 시도했다'는 해양경찰청의 발표에 대해 "명예와 인격을 살인하는 자들"이라며, 강하게 반발했습니다.  이래진 씨는 어젯밤(22일) 자신의 SNS를 통해 "해경이 발표한 모든 내용을 정확히 찝어서 반박을 얼마든지 할 수 있다"며 이같이 밝혔습니다.  또 "초라한 선상 위령제를 다녀오고 인천항에 도착하자마자 잔인하게 숨어서 비공개하면서 여론전을 하자는 게 뭔가"라고 비판했습니다.  이어 "비공개 했던 조카의 편지를 공개할 수밖에 없다"며, 숨진 공무원의 아들이 문 대통령에 보낸 답장을 공개했습니다.  숨진 공무원의 아들은 답장에서 "책임을 물을 것은 묻고, 억울한 일이 있다면 당연히 명예를 회복해야 한다는 대통령님의 말씀과 직접 챙기겠다는 약속을 믿는다"며, "아빠는 잃었지만 어떤 분이신지 너무 잘 알기에 명예까지 잃을 수는 없다"고 썼습니다.  또 "저희 가족이 겪고 있는 지금 이 고통이 하루빨리 끝나길 바라며, 대통령님의 말씀을 가슴에 새기고 그 약속을 믿고 기다리겠다"고 적었습니다.  해경은 어제 오후 열린 기자간담회에서 피살된 공무원이 인터넷 도박 등으로 채무에 시달린 끝에 현실 도피 목적으로 월북을 시도한 것으로 판단된다고 밝혔습니다.[사진 출처 : 연합뉴스]홍성희 (bombom@kbs.co.kr )','정치','','KBS','http://news.kbs.co.kr/news/view.do?ncd=5031989&ref=A')
입력 실패
INSERT INTO 일반 VALUES('[속보]'묻지마 폭행' 당하는 119 구급대원 매년 200여건 발생','2020.10.23. 오전 12:33','119 구급대원이 이유없이 무차별 폭행 당하는 사례가 매년 200여건 발생하는 것으로 나타났다.또 소방공무원 특수건강검진 결

입력 실패
INSERT INTO 일반 VALUES('[여론조사]더불어민주 당내 선호도 이낙연 1위…국민의힘 지지자 29.1% 윤석열 꼽아','2020.10.23. 오전 12:32',' 강원도민들은 비록 오차범위(95% 신뢰수준에 ±3.4%포인트) 내이지만 차기 대선 적합자로 이재명 경기도지사를 1순위로 꼽았다.  그러나 더불어민주당 지지층에서는 이낙연 당대표가 44.2%를 얻어 이 지사(30.5%)를 오차범위 밖에서 앞섰다. 대중적인 지지도는 이재명 지사가 높지만 정작 민주당 내에서는 이낙연 대표의 선호도가 높은 것이다. 당 내부 경선을 승리해야 본선에 진출할 수 있다는 점에서 이 지사는 당심(黨心) 확보에 더 많은 노력을 기울여야 할 것으로 분석된다.   도내에서 이 지사는 삼척권(19.4%), 40대(27.0%)·50대(22.3%), 남성(20.2%), 블루칼라(22.5%)·자영업(22.4%)에서 지지도가 전체 평균보다 상대적으로 높았다. 반면 이 대표는 삼척권(20.1%), 40대(25.6%) 및 30대(22.3%), 화이트칼라(20.4%), 고소득층(18.6%)에서 지지세가 형성됐다.   국민의힘 지지자들은 윤석열 총장(29.1%)을 후보로 꼽았고 홍준표 국회의원(11.8%)이 뒤를 이었다. 원희룡 제주도지사(7.4%), 황교안 전 대표(6.2%), 오세훈(4.7%), 안철수(4.0%) 등이 한 자릿수 지지율을 얻으며 순위권에 들었다.  그러나 20.4%가 '적합한 후보가 없다'고 밝혀 추후 이들의 선택이 국민의힘 후보 선정에 적지 않은 영향을 미칠 전망이다.특이한 점은 도내의 정의당 지지자들은 같은 당 심상정 국회의원(8.4%)보다 이재명 지사(34%)를 더 선호했다는 점이다. 이낙연 대표에게도 9.5%가 지지 의사를 밝혔다. 민주당 계열로 분류되는 열린민주당은 이재명(52.2%), 이낙연(47.8%)에게 확실한 지지를 보냈다. 이하늘기자ⓒ 강원일보 - www.kwnews.co.kr','정치','','강원일보','http://www.kwnews.co.

...

INSERT INTO 일반 VALUES('전세대란 추가대책 놓고 홍남기-김현미 시각차','2020.10.21. 오후 5:55',' 이낙연 더불어민주당 대표가 소집한 경제상황점검회의에서 홍남기 경제부총리 겸 기획재정부 장관과 김현미 국토교통부 장관이 부동산 전세대란에 대한 추가 대책을 놓고 미묘한 시각 차이를 드러냈다. 앞서 이 대표가 당내 부동산 태스크포스(TF)를 출범시키며 관련 정책을 주도하겠다는 뜻을 보인 가운데 정부가 어떤 후속 대책을 내놓을지 주목된다.21일 국회에서 열린 경제상황점검회의에서 홍 부총리는 전세 시장과 관련해 "가격은 오르고 대상 물량은 줄었는데 실거래 통계는 전년 대비 늘고 있다"며 "실수요자와 서민 보호를 위한 안정화 노력에 총력을 기울이겠다"고 밝혔다. 전세 시장 안정을 위해 당정 협의를 거쳐 조만간 추가 대책을 내놓을 수 있다는 뜻으로 해석되는 대목이다. 김 장관도 회의에서 전세가격 등 부동산 관련 지표와 전세난 여론 등을 보고하면서 홍 부총리와 시장 모니터링을 강화하며 대책을 마련해야 한다는 취지에 공감했다. 그러나 총력을 다하겠다고 한 홍 부총리와 달리 김 장관은 시장 상황을 더 지켜보면서 정책 효과를 보자는 뉘앙스에 가까워 참석자들이 두 사람 간 시각에 온도차를 느낀 것으로 전해졌다.홍 부총리는 우리 경제가 국제금융 등 대외 부문에서 잘 대응해 왔지만 부동산 시장과 가계부채가 문제라고 지적하며 대내적 리스크 요인에 대해 신속한 대응이 필요하다고 강조했다. 그는 현재 경제 상황과 관련해 "모든 성과는 당의 전폭적인 협조와 협업 없이 짧은 시간 안에 이루기 어렵다"며 적극적인 지원을 요청했다.이와 관련해 허영 민주당 대변인은 "전세 시장에 대한 데이터는 좀 더 지켜봐야 할 상황"이라며 "다음주 당내 부동산 TF 회의를 통해 추가 논의가 이뤄질 것"이라고 말했다.앞서 민주당은 이 대표 지시로 부동산 정책 개발을 위한 TF인 미래주거추진단을 출범시켰다. 추진단은 다음주 첫 회의를 개최하고 관련 정책을 논의할 계획이다. 한편 이날 민

INSERT INTO 일반 VALUES('`소신감사` 최재형, 감사위원 선임도 강행할까','2020.10.21. 오후 5:54','감사원이 지난 20일 월성 1호기 폐쇄 조치 관련 감사 결과를 공개한 가운데 논란의 중심에 섰던 최재형 감사원장의 향후 행보에 관심이 쏠린다. 공석으로 남은 감사위원 임명 등을 둘러싸고 최 원장이 청와대와 다시 갈등을 겪을 수도 있다는 예측이 나온다.최 원장이 당면한 과제는 현재 6개월째 공석인 감사위원직 한 자리에 대한 임명 제청이다. 지난 4월 이준호 전 감사위원이 퇴임한 뒤 최 원장과 청와대 간 팽팽한 신경전이 이어지고 있다. 청와대에서는 최 원장이 제청한 인사를 거부했고, 최 원장도 청와대가 추천한 김오수 전 법무부 차관을 '코드 인사'라는 이유로 반대한 것으로 알려졌다. 감사위원회 의결은 과반수 동의를 원칙으로 이뤄진다. 현재 6명의 감사위원 중 3명이 친여 성향으로 알려져 있어 최 원장과 청와대 모두 남은 한 자리에 어떤 성향의 인사가 오느냐가 매우 중요한 상황이다. 최 원장은 지난 15일 국회 국정감사에서 "감사의 결론이 나면 임명권자와 적극 상의해 이런 문제가 조속히 해결될 수 있도록 노력하겠다"고 밝혔다.앞으로 다른 원전이 폐쇄되는 때나 이미 백지화된 신규 원전 6기에 대한 결정 타당성도 감사 대상에 오를 수 있다는 전망이 제기된다. 감사 방향에 따라 최 원장과 청와대 간 갈등이 재점화할 소지가 있다. 여권을 중심으로 한 '최 원장 경질론'도 다시 대두할 수 있다.[안정훈 기자 / 박제완 기자][ⓒ 매일경제 & mk.co.kr, 무단전재 및 재배포 금지]	','정치','','매일경제','http://news.mk.co.kr/newsRead.php?no=1080783&year=2020')
입력 실패
INSERT INTO 일반 VALUES('與최인호 "이헌재가 펀드로비 중심"','2020.10.21. 오후 5:54',' 최인호 더불어민주당 수석대변인(사진)이 옵티머스 고문을 맡은 이헌재 전 경제부총리를 향해 "금융사기꾼

INSERT INTO 일반 VALUES('이낙연 "北, 코로나 방역 협력하자…日, 징용 협의 타결 기대"(종합)','2020.10.21. 오후 5:51','[서울=뉴시스]김지훈 윤해리 기자 = 이낙연 더불어민주당 대표가 21일 북한에 신종 코로나바이러스 감염증(코로나19) 방역·보건 협력을 제안했다. 일제강점기 강제징용 배상 문제와 관련해서는 한일 양국의 의지만 있다면 접점을 찾을 수 있을 거로 기대했다. 이 대표는 이날 오후 서울 중구 프레스센터에서 열린 외신기자 초청 간담회 기조연설에서 "한반도는 항구적 평화를 확보해야 한다"라며 "우선은 방역과 보건에서 남북 간 협력을 시작하자고 북측에 제안한다"고 밝혔다. 이 대표는 "한국만이 아니라 한반도 전체가 코로나 청정지역이 되는 날이 하루라도 빨리 오기를 소망한다"고 말했다. 더불어 "코로나 위기에서 한국은 국제사회와 함께하겠다"며 "방역의 경험과 임상데이터를 공유하고, 치료제와 백신의 개발을 위해 국제사회와 협력하겠다. 개발도상국을 위한 치료제와 백신 공급을 지원하겠다"고 밝혔다. 이어 "그런 목적의 국제펀드를 조성하는 방안을 국제사회에 제안한다"고 말했다. 이 대표는 한일관계 최대 현안인 강제징용 배상 문제 해결 의지도 분명히 했다. 그는 "아베 총리 재임 중에 있었던 한일 정상 간의 합의, 또 제가 작년 10월 도쿄에 가서 아베 총리와 만났을 때 있었던 합의는 외교 당국 간 협의를 진행한다는 것"이라며 "그 합의로 돌아가서 외교 당국 간 합의를 촉진시키는 것이 가장 현실적이고 효과적인 방법이 될 것"이라고 전제했다. 그는 "그동안에는 아쉽게도 외교 당국 간 회담이 진행됐다가 중지되는 과정이 반복됐다. 제가 보기엔 주로 일본측 총리 관저에 의해서 제동이 걸리곤 했다고 생각한다. 두 나라 정부 모두 외교 당국 간 협의에 맡기고 웬만하면 제동을 걸지 안으면 좋은 결과가 나올 수 있으리라 생각한다"며 외교 당국에 권한을 줘야 하는 이유를 설명하기도 했다. 이 대표는 "오늘 오전에 국정감사에서 주일 한국대사에게 확

INSERT INTO 일반 VALUES('김근식 “그 많은 ‘김남국들’이 설치니…금태섭이 나가지”','2020.10.21. 오후 5:48','국민의힘 송파병 당협위원장인 김근식 경남대 교수가 21일 더불어민주당 김남국 의원을 향해 “제발 철 좀 드시라”며 금태섭 전 의원 탈당의 한 원인이라고 지목했다.김 교수는 이날 페이스북에 금 전 의원을 향한 김 의원의 모순된 입장을 지적한 기사를 링크하고 이같이 밝혔다.앞서 금 전 의원은 이날 “민주당은 예전의 유연함과 겸손함, 소통의 문화를 찾아 볼 수 없을 정도로 변했다. 더 이상은 당이 나아가는 방향을 승인하고 동의할 수 없는 지경에 이르렀다”며 탈당을 선언했다.이에 김 의원은 금 전 의원을 향해 “자신의 이익과 자리만 쫓아다니는 철새 정치인”이라며 “ 유아적 수준의 이기적인 모습”이라고 맹비난했다. 다만 김 의원은 지난 6월 언론 인터뷰에서 금 전 의원을 닮은 소신 있는 정치인이 되겠다고 다짐한 바 있다.이 같은 김 의원의 태세 전환에 김 교수는 “이래서 금태섭 의원이 나가는 것”이라며 “그 많은 ‘김남국들’이 설치니 민주당에는 희망이 없다”고 지적했다.이어 “(김 의원은) 타고난 대깨문(문재인 대통령 극성 지지자)으로 조국 사수에 혈안이 됐다가, 조국 비판하는 금태섭 쫓아내겠다고 강서갑 출마 선언했다가, 친문 선봉 덕에 갑자기 안산 공천 받고, 그 덕에 엉겁결에 (국회의원) 배지 달았다”고 꼬집었다.특히 “배지 달고도 정권의 친위대가 돼 조국에 이은 추미애 수호천사 노릇하고 국회에서 천지분간 못하고 홍위병 자처하니 가관도 그런 가관이 없다”고 비판했다.또 “당선되고 폼 잡을 때는 당내 쓴소리하는 금태섭 본받겠다고 하고, 이제 탈당하는 금태섭에게 철새라고 모욕을 해대는 김남국 의원”이라고 지칭하며 “‘꼬마 정청래’, ‘꼬마 홍위병’ 노릇 그만하시라”고 다그쳤다.아울러 “최소한 이낙연 대표의 의례적 워딩이라도 읽어보시라”며 “대깨문 선봉에 서는 그 많은 ‘김남국들’ 때문에 민주당에는 희망이 없는 것”이라고 재차 강조

입력 성공
INSERT INTO 일반 VALUES('[정치실록] "편 가르기, 오만한 태도"..."국민의힘의 도돌이표 정쟁"','2020.10.21. 오후 5:45','1. "(민주당은) 편 가르기로 국민들을 대립시키고 생각이 다른 사람을 범법자, 친일파로 몰아붙이며 윽박지르는 오만한 태도가 가장 큰 문제" (금태섭 더불어민주당 전 의원, 페이스북 글에서 더불어민주당에 탈당계를 제출한다고 밝히며)2. "탈당이라는 방식으로 당의 마지막 충정을 보여주겠다는 말씀도 이해는 되지만 동의하기 어렵습니다" (박용진 더불어민주당 의원, 페이스북 글에서 금태섭 전 의원의 탈당과 관련하여 당 안에서 소신있게 행동하며 변화를 이끌겠다고 밝히며) 3. "관심 없다. 나는 내 할 일만 하면 되는 사람" (김종인 국민의힘 비상대책위원장, 기자들과 만나 비대위 체제를 끝내야한다는 조경태 국민의힘 의원의 주장에 대해)4. "현장과 정책 사이에 괴리가 있는 만큼 현장을 더욱더 챙겨야 한다" (이낙연 더불어민주당 대표, 국회 경제상황 점검회의에서 경제 부처 장관들에게 경제 정책의 괴리를 지적하며) 5. "민주당의 인내와 선의를 조건 걸기로 화답하는 국민의힘의 도돌이표 정쟁에 유감" (김태년 더불어민주당 원내대표, 당 최고위원회의에서 특검과 공수처를 동시에 추진하자는 국민의힘의 주장을 일축하며)6. "희대의 사기 피의자 말에 아전인수와 내로남불을 보여주고 있다" (김종철 정의당 대표, 정의당 8주년 기념식에서 김봉현 전 스타모빌리티 회장의 옥중 서신을 입맛에 맞게 해석하는 거대 양당이라 지적하며)7. "보수진영뿐만 아니라 중도진영, 더 나아가 정당을 달리하는 분들도 함께 할 수 있는 공간이 만들어지길 바란다" (오신환 국민의힘 전 의원, '하우스' 미디어 쇼케이스에서 국민의힘 인사들의 정치카페 '하우스'를 개업하며)[안현호 인턴기자][ⓒ 매일경제 & mk.co.kr, 무단전재 및 재배포 금지]	','정치','','매일경제','http://raythep.mk.co.kr/newsView.php?